<a href="https://colab.research.google.com/github/andrewlee1234567/lab2/blob/main/Part_6.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
from google.colab import drive
drive.mount('/content/drive', force_remount=True)

Mounted at /content/drive


In [ ]:
pip install lonboard

In [ ]:
import numpy as np
import pandas as pd
import geopandas as gpd
# This is a super popular library for working with ML and DL algorithms.
from sklearn.cluster import KMeans, DBSCAN
import matplotlib.pyplot as plt
import shapely
import folium
import seaborn as sns
from lonboard import Map, ScatterplotLayer

In [ ]:
parcels=gpd.read_file("/content/Chicago_parcels.shp")

In [ ]:
parcels.head()
parcels.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
RangeIndex: 592521 entries, 0 to 592520
Data columns (total 6 columns):
 #   Column    Non-Null Count   Dtype   
---  ------    --------------   -----   
 0   POLY_ID   592521 non-null  int64   
 1   ID        592521 non-null  int64   
 2   AREA      592521 non-null  float64 
 3   PIN_OLD   592521 non-null  int64   
 4   PIN       592521 non-null  int64   
 5   geometry  592521 non-null  geometry
dtypes: float64(1), geometry(1), int64(4)
memory usage: 27.1 MB


In [ ]:
parcels.shape

(592521, 6)

In [ ]:
parcels.columns

Index(['POLY_ID', 'ID', 'AREA', 'PIN_OLD', 'PIN', 'geometry'], dtype='object')

In [ ]:
parcels.total_bounds

array([1091173.15922881, 1813913.37750871, 1205119.21461458,
       1952997.78968386])

In [ ]:
ld_bbox = [1091173.15922881, 1813913.37750871, 1205119.21461458,1952997.78968386]

In [ ]:
parcels=parcels[parcels.intersects(shapely.box(*ld_bbox))]

In [ ]:
parcels.shape

(592521, 6)

In [ ]:
from lonboard import Map, SolidPolygonLayer
from lonboard import Map, SolidPolygonLayer

In [ ]:
layer = SolidPolygonLayer.from_geopandas(parcels)
map = Map(layers=[layer], _height=500)
map

/usr/local/lib/python3.10/dist-packages/lonboard/_layer.py:112: UserWarning: GeoDataFrame being reprojected to EPSG:4326
  warnings.warn("GeoDataFrame being reprojected to EPSG:4326")


Map(layers=[SolidPolygonLayer(table=pyarrow.Table
POLY_ID: uint32
ID: uint32
AREA: float
PIN_OLD: int32
PIN: i…

In [ ]:
parcels['longitude']=parcels['geometry'].centroid.x
parcels['latitude']=parcels['geometry'].centroid.y
parcels.head(1)

POLY_ID  ID  AREA    PIN_OLD        PIN  \
0        1  93  0.01  836300010  836300010   

                                            geometry     longitude  \
0  POLYGON ((1091182.694 1942890.287, 1091173.159...  1.091780e+06   

       latitude  
0  1.943042e+06

In [ ]:
geometry = gpd.points_from_xy(parcels.latitude,parcels.longitude)
gdf_parcels = gpd.GeoDataFrame(parcels, geometry=geometry)
gdf_parcels.head()

POLY_ID  ID  AREA    PIN_OLD        PIN                         geometry  \
0        1  93  0.01  836300010  836300010  POINT (1943041.685 1091780.062)   
1        2  94  0.00  836300011  836300011  POINT (1943134.441 1092426.507)   
2        3  96  0.02  836300013  836300013  POINT (1942695.301 1091688.490)   
3        4  95  0.01  836300012  836300012  POINT (1942342.716 1091538.184)   
4        5  92  0.01  836300009  836300009  POINT (1942082.620 1091543.397)   

      longitude      latitude  
0  1.091780e+06  1.943042e+06  
1  1.092427e+06  1.943134e+06  
2  1.091688e+06  1.942695e+06  
3  1.091538e+06  1.942343e+06  
4  1.091543e+06  1.942083e+06

In [ ]:
latitude=parcels.latitude
longitude=parcels.longitude
AREA=parcels.AREA
columns_of_interest = ['latitude', 'longitude', 'AREA']
correlation_matrix = parcels[columns_of_interest].corr()
sns.heatmap(correlation_matrix, annot=True)
plt.show()

In [ ]:
kmeans=KMeans(n_clusters=100).fit(np.array(gdf_parcels[['latitude','longitude']]))

/usr/local/lib/python3.10/dist-packages/sklearn/cluster/_kmeans.py:870: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  warnings.warn(


In [ ]:
parcels2 = gpd.GeoDataFrame(kmeans.cluster_centers_, columns=['latitude', 'longitude'])

In [ ]:
gdf_parcels.groupby('ID').size().plot(kind='barh', color=sns.palettes.mpl_palette('Dark2'))

In [ ]:
categories = gdf_parcels['ID'].unique()
colors = sns.color_palette("bright", len(categories))
colors

In [ ]:
color_dict = dict(zip(categories, colors))
color_array = np.array([tuple(np.append(np.multiply(color_dict.get(x, (0, 0, 0)), 255).astype(int), 255)) for x in gdf_parcels['ID']], dtype=np.uint8)
color_array
layer.radius_scale = 40
layer.opacity = 0.05
layer.get_fill_color = color_array

In [ ]:
kmeans = KMeans(n_clusters=5, random_state=42)
gdf_parcels['kmeans_cluster'] = kmeans.fit_predict(gdf_parcels[['AREA']])

/usr/local/lib/python3.10/dist-packages/sklearn/utils/validation.py:767: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if not hasattr(array, "sparse") and array.dtypes.apply(is_sparse).any():
/usr/local/lib/python3.10/dist-packages/sklearn/utils/validation.py:605: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype):
/usr/local/lib/python3.10/dist-packages/sklearn/utils/validation.py:614: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype) or not is_extension_array_dtype(pd_dtype):
/usr/local/lib/python3.10/dist-packages/sklearn/cluster/_kmeans.py:870: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  w

In [ ]:
from sklearn.cluster import DBSCAN

In [ ]:
dbscan = DBSCAN(eps=0.005, min_samples=40)
gdf_parcels['dbscan_cluster'] = dbscan.fit_predict(gdf_parcels[['AREA']])

In [ ]:
fig, axes = plt.subplots(1, 2, figsize=(14, 8))

In [ ]:
gdf_parcels.plot(ax=axes[0], column='kmeans_cluster', categorical=True, legend=True, markersize=1, alpha=0.5, cmap='Set1')
axes[0].set_title('K-means Clustering')
gdf_parcels.plot(ax=axes[1], column='dbscan_cluster', categorical=True, legend=False, markersize=1, alpha=0.5, cmap='viridis')
axes[1].set_title('DBSCAN Clustering')

In [ ]:
plt.show()


In [ ]:
layer_1 = ScatterplotLayer.from_geopandas(gdf_parcels)
map_1 = Map(layers=[layer_1], _height=400)
map_1

/usr/local/lib/python3.10/dist-packages/lonboard/_layer.py:112: UserWarning: GeoDataFrame being reprojected to EPSG:4326
  warnings.warn("GeoDataFrame being reprojected to EPSG:4326")


Map(layers=[ScatterplotLayer(table=pyarrow.Table
POLY_ID: uint32
ID: uint32
AREA: float
PIN_OLD: int32
PIN: in…

In [ ]:
categories_kmeans = gdf_parcels['kmeans_cluster'].unique()
colors_kmeans = sns.color_palette("bright", len(categories_kmeans))
color_dict_kmeans = dict(zip(categories_kmeans, colors_kmeans))
color_array_kmeans = np.array([tuple(np.append(np.multiply(color_dict_kmeans.get(x, (0, 0, 0)), 255).astype(int), 255)) for x in gdf_parcels['kmeans_cluster']], dtype=np.uint8)
layer_1.radius_scale = 50
layer_1.opacity = 0.05
layer_1.get_fill_color = color_array_kmeans

In [ ]:
layer_2 = ScatterplotLayer.from_geopandas(gdf_parcels)
map_2 = Map(layers=[layer_2], _height=400)
map_2

/usr/local/lib/python3.10/dist-packages/lonboard/_layer.py:112: UserWarning: GeoDataFrame being reprojected to EPSG:4326
  warnings.warn("GeoDataFrame being reprojected to EPSG:4326")


Map(layers=[ScatterplotLayer(table=pyarrow.Table
POLY_ID: uint32
ID: uint32
AREA: float
PIN_OLD: int32
PIN: in…

In [ ]:
dbscan = DBSCAN(eps=0.005, min_samples=40)
gdf_parcels['dbscan_cluster'] = dbscan.fit_predict(gdf_parcels[['AREA']])
print(gdf_parcels['dbscan_cluster'].value_counts())

/usr/local/lib/python3.10/dist-packages/sklearn/utils/validation.py:767: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if not hasattr(array, "sparse") and array.dtypes.apply(is_sparse).any():
/usr/local/lib/python3.10/dist-packages/sklearn/utils/validation.py:605: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype):
/usr/local/lib/python3.10/dist-packages/sklearn/utils/validation.py:614: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype) or not is_extension_array_dtype(pd_dtype):


In [ ]:
categories_dbscan = gdf_parcels['dbscan_cluster'].unique()
colors_dbscan = sns.color_palette("bright", len(categories_dbscan))
color_dict_dbscan = dict(zip(categories_dbscan, colors_dbscan))
color_array_dbscan = np.array([tuple(np.append(np.multiply(color_dict_dbscan.get(x, (0, 0, 0)), 255).astype(int), 255)) for x in gdf_parcels['dbscan_cluster']], dtype=np.uint8)
layer_2.radius_scale = 50
layer_2.opacity = 0.05
layer_2.get_fill_color = color_array_dbscan

KeyError: ignored